In [1]:
%load_ext sql
%sql sqlite:///CourseDataWarehouse.db

'Connected: @CourseDataWarehouse.db'

In [2]:
%%sql
ATTACH 'DWETL.db' AS CDDB

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [3]:
%%sql
select * from CDDB.PROGRAMS LIMIT 1

 * sqlite:///CourseDataWarehouse.db
Done.


[(1, 'AN', 'Asian Studies')]

In [19]:
%%sql

DROP TABLE IF EXISTS PROGRAMS_DIM;
DROP TABLE IF EXISTS LOCATIONS_DIM;
DROP TABLE IF EXISTS TIMES_DIM;
DROP TABLE IF EXISTS FACULTY_DIM;
DROP TABLE IF EXISTS COURSE_CATALOGS_DIM;
DROP TABLE IF EXISTS COURSES_FACT;





vacuum; 

CREATE TABLE PROGRAMS_DIM (
    PID INTEGER NOT NULL PRIMARY KEY,
    program_code TEXT NOT NULL,
    program_name TEXT NOT NULL
);


CREATE TABLE LOCATIONS_DIM (
    LID INTEGER PRIMARY KEY,
    location TEXT ,
    BuildingName TEXT

);


CREATE TABLE FACULTY_DIM (
    FID  INTEGER NOT NULL PRIMARY KEY,
    instructor_fname TEXT NOT NULL,
    instructor_lname TEXT NOT NULL
);


CREATE TABLE COURSE_CATALOGS_DIM (
    CID INTEGER PRIMARY KEY,
    Catalog_ID TEXT NOT NULL,
    CatalogYear TEXT NULL,
    Credits TEXT  NULL,
    Prereqs TEXT,
    Coreqs TEXT,
    Fees INTEGER,
    Description TEXT,
    Attributes TEXT
);



CREATE TABLE COURSES_FACT (
    CID INTEGER NULL ,
    CRN INTEGER NOT NULL,
    SEMESTER TEXT NOT NULL ,
    YEAR INTEGER NOT NULL,
    Title TEXT  NULL,
    SECTION TEXT NOT NULL,
    Act INTEGER,
    Cap INTEGER,
    Rem INTEGER, 
    timecodes TEXT,
    PID INTEGER  NULL,
    LID INTEGER  NULL,
    FID INTEGER  NULL,
   Catalog_ID  TEXT NULL ,
    FOREIGN KEY (PID) REFERENCES PROGRAMS_DIM (PID),
    FOREIGN KEY (LID) REFERENCES LOCATIONS_DIM (LID),
    FOREIGN KEY (FID) REFERENCES FACULTY_DIM (FID),
    FOREIGN KEY (CID) REFERENCES COURSE_CATALOGS_DIM (CID)
);

 * sqlite:///CourseDataWarehouse.db
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.


[]

In [14]:
%%sql 
SELECT count(FID) 
FROM (SELECT FID, instructor_lname,instructor_fname,COURSES_FACT.Catalog_ID,program_name, Title ,sum(act), sum(cap), sum(rem) , YEAR,SEMESTER , COUNT(CRN) as COURSESTaught
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
     left JOIN COURSE_CATALOGS_DIM USING (CID)
    left  JOIN PROGRAMS_DIM USING (PID)
WHERE (instructor_lname like '%Huntley%') and YEAR IS 2018
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC
);

 * sqlite:///CourseDataWarehouse.db
Done.


[(0,)]

In [15]:
%%sql
SELECT * FROM  PROGRAMS_DIM
where program_code like "BA"
LIMIT 10

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [20]:
%%sql 


INSERT INTO PROGRAMS_DIM ( program_name, program_code)
SELECT DISTINCT  program_name, program_code
FROM CDDB.PROGRAMS;


INSERT INTO LOCATIONS_DIM (location ,BuildingName )
SELECT  location , BuildingName
FROM CDDB.LOCATION;


INSERT INTO FACULTY_DIM (instructor_fname , instructor_lname)
SELECT  DISTINCT instructor_fname , instructor_lname
FROM CDDB.FACULTY;


INSERT INTO COURSE_CATALOGS_DIM (Catalog_ID,CatalogYear, credits, Prereqs, Coreqs, Fees, Description, Attributes)
SELECT catalog_ID,CDDB.COURSE.CatalogYear , credits, prereqs, coreqs, fees, description, attributes
FROM CDDB.COURSE;



INSERT INTO COURSES_FACT (Catalog_ID , CRN, SEMESTER , YEAR , TITLE, SECTION, ACT, CAP,REM, TIMECODES, PID, LID, FID, CID)
SELECT DISTINCT CDDB.COURSE_OFFERING.Catalog_ID, CDDB.CLASS_MEETINGS.CRN, CDDB.CLASS_MEETINGS.SEMESTER , CDDB.CLASS_MEETINGS.YEAR, CDDB.COURSE_OFFERING.title, CDDB.COURSE_OFFERING.SECTION, act, cap, rem, timecodes, PROGRAMS_DIM.PID, LOCATIONS_DIM.LID, FID,CDDB.COURSE.CID
FROM CDDB.COURSE_OFFERING
     JOIN CDDB.CLASS_MEETINGS USING  (COID)
    left JOIN LOCATIONS_DIM USING (LID)
     left JOIN CDDB.COURSE USING (CID)
    left JOIN PROGRAMS_DIM USING (PID)
    left JOIN FACULTY_DIM USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID);
    
    

    
   

 * sqlite:///CourseDataWarehouse.db
92 rows affected.
207 rows affected.
1104 rows affected.
6696 rows affected.
13756 rows affected.


[]

In [21]:
%%sql
SELECT FID, instructor_lname,instructor_fname,COURSE_CATALOGS_DIM.CatalogYear,COURSES_FACT.Catalog_ID,program_name, Title ,sum(act), sum(cap), sum(rem) , YEAR,SEMESTER , COUNT(CRN) as COURSESTaught
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
     left JOIN COURSE_CATALOGS_DIM USING (CID)
    left  JOIN PROGRAMS_DIM USING (PID)
WHERE (instructor_lname like '%Huntley%')
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC


 * sqlite:///CourseDataWarehouse.db
Done.


[(275, 'Huntley', 'Christopher L.', '2018_2019', 'BA0510', 'Business Analytics', 'Databases for Business Analytics', 68, 64, -4, 2019, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', '2018_2019', 'OM0101', 'Operations Management', 'Operations Management', 53, 50, -3, 2019, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', '2017_2018', 'IS0260', 'Information Systems', 'Database Systems', 24, 25, 1, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2018_2019', 'OM0101', 'Operations Management', 'Operations Management', 49, 50, 1, 2018, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', '2018_2019', 'BA0505', 'Business Analytics', 'Python for Business Analytics', 27, 20, -7, 2018, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2017_2018', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 22, 25, 3, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2017_2018', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 20, 25, 5, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2017_2018', 'IS0510', 'Information Systems', 'Databases for Business Analytics', 18, 20, 2, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2016_2017', 'OM0101', 'Operations Management', 'Operations Management', 28, 29, 1, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2017_2018', 'IS0505', 'Information Systems', 'Python for Business Analytics', 28, 20, -8, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2017_2018', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 23, 25, 2, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2016_2017', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 25, 25, 0, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2016_2017', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 7, 25, 18, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2016_2017', 'IS0585C', 'Information Systems', 'Contemporary Topics: Database Systems for Business Analytics', 30, 40, 10, 2016, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', '2015_2016', 'IS0585', 'Information Systems', 'Contemporary Topics: Information Systems and Data', 15, 20, 5, 2016, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', '2016_2017', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 15, 25, 10, 2016, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2015_2016', 'OM0101', 'Operations Management', 'Operations Management', 57, 58, 1, 2016, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', '2016_2017', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 23, 25, 2, 2016, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2015_2016', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 21, 25, 4, 2015, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', '2015_2016', 'IS0100', 'Information Systems', 'Intro to Information Systems', 56, 58, 2, 2015, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', '2015_2016', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 13, 25, 12, 2015, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', None, 'IS0135', None, 'Fundamentals of Web Design', 26, 25, -1, 2014, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', None, 'IS0100', None, 'Intro to Information Systems', 26, 25, -1, 2014, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', None, 'IS0320', None, 'Systems Design and Implementation', 16, 25, 9, 2014, 'Fall', 1)]

In [11]:
%%sql
SELECT FID, instructor_lname,instructor_fname,COURSES_FACT.Catalog_ID,program_name, Title ,sum(act), sum(cap), sum(rem) , YEAR,SEMESTER , COUNT(CRN) as COURSESTaught
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
     left JOIN COURSE_CATALOGS_DIM USING (CID)
    left  JOIN PROGRAMS_DIM USING (PID)
WHERE (instructor_lname like '%Huntley%') and YEAR IS 2018
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC


 * sqlite:///CourseDataWarehouse.db
Done.


[(275, 'Huntley', 'Christopher L.', 'IS0260', 'Information Systems', 'Database Systems', 24, 25, 1, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 49, 50, 1, 2018, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', 'BA0505', 'Business Analytics', 'Python for Business Analytics', 27, 20, -7, 2018, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 22, 25, 3, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 20, 25, 5, 2018, 'Spring', 1)]

In [8]:
%%sql
SELECT instructor_lname,instructor_fname ,CatalogYear, COURSES_FACT.Catalog_ID,PROGRAMS_DIM.program_name,PROGRAMS_DIM.program_code, Title ,SECTION  ,CRN, SEMESTER , YEAR , ACT, CAP,REM, TIMECODES
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
    left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC;





 * sqlite:///CourseDataWarehouse.db
Done.


[('Lakeland', 'Paul F.', None, 'RS 0268', None, None, 'American Catholic History', '01', 38873, 'Spring', 2019, 25, 25, 0, "['TF 1100am-1215pm 01/22-04/30 CNS 304']"),
 ('Cassidy', 'Kevin J.', None, 'PO 0233', None, None, 'American Political Thought', '01', 38728, 'Spring', 2019, 22, 25, 3, "['MR 1100am-1215pm 01/22-04/30 CNS 103']"),
 (' Bagirov', 'Feyzi', None, 'BA 0540', None, None, 'Business Intelligence', '01', 39007, 'Spring', 2019, 30, 30, 0, "['R 0630pm-0930pm 03/25-05/10 DSB 115']"),
 (' Li', 'Danke', None, 'HI 0102', None, None, 'China, Japan, and Europe', '01', 38788, 'Spring', 2019, 25, 25, 0, "['TF 0200pm-0315pm 01/22-04/30 DMH 347']"),
 ('Rusu', 'Amalia I.', None, 'CS 0351L', None, None, 'Computer Science Junior Clinic II', '01', 38886, 'Spring', 2019, 7, 20, 13, "['R 0930am-1020am 01/22-04/30 BNW 131']"),
 ('Drake', 'Ryan T.', None, 'PH 0224', None, None, 'Critical Thinking', '01', 38856, 'Spring', 2019, 21, 20, -1, "['TF 0930am-1045am 01/22-04/30 CNS 104']"),
 ('Post', 'Jed Morgan', None, 'SA 0140', None, None, 'Darkroom Photography', '01', 38773, 'Spring', 2019, 13, 15, 2, "['F 1100am-0130pm 01/22-04/30 LYL 20']"),
 (' Tao', 'Jie', None, 'BA 0545', None, None, 'Data Mining', '01', 39008, 'Spring', 2019, 21, 30, 9, "['M 0630pm-0930pm 01/22-05/10 DSB 115']"),
 ('Huntley', 'Christopher L.', None, 'BA 0510', None, None, 'Databases for Business Analytics', '01', 39006, 'Spring', 2019, 34, 32, -2, "['T 0630pm-0930pm 01/28-03/15 DSB 105', 'S 0900am-0400pm 02/02-02/02 DSB 115', 'S 0900am-0400pm 02/16-02/16 DSB 115', 'S 0900am-0400pm 03/09-03/09 DSB 115']"),
 ('Rose', 'Marice E.', None, 'HR 0204', None, None, 'Emerging Questions', '01', 38999, 'Spring', 2019, 23, 25, 2, "['TF 1100am-1215pm 01/22-04/30 CNS 10']"),
 ('McFadden', 'David W.', None, 'HI 0103', None, None, 'Europe, Russia, and the World, 1300-1918', '01', 38789, 'Spring', 2019, 25, 25, 0, "['TF 1230pm-0145pm 01/22-04/30 CNS 305']"),
 ('Wills', 'Margaret A.', None, 'CO 0350', None, None, 'Family Crisis Communication', '01', 38836, 'Spring', 2019, 19, 20, 1, "['MR 1230pm-0145pm 01/22-04/30 DMH 350']"),
 ('Downie', 'David L.', None, 'HR 0304', None, None, 'Finding Answers', '01', 39003, 'Spring', 2019, 24, 25, 1, "['T 0630pm-0900pm 01/22-04/30 DMH 149']"),
 ('Rosenfeld', 'Gavriel D.', None, 'HI 0112', None, None, 'Germany Between Dictatorship and Democracy', '01', 38794, 'Spring', 2019, 23, 25, 2, "['TF 0930am-1045am 01/22-04/30 CNS 1']"),
 (' Iddins', 'Anne', None, 'CO 0352', None, None, 'Global Mediated Activism', '01', 38837, 'Spring', 2019, 16, 17, 1, "['M 0800am-1030am 01/22-04/30 DMH 148']"),
 (' Marsans-Sakly', 'Silvia', None, 'HI 0106', None, None, 'Imperialism and Colonialism in World History, 1500-Present', '01', 38791, 'Spring', 2019, 18, 25, 7, "['MR 0930am-1045am 01/22-04/30 DMH 149']"),
 ('Downie', 'David L.', None, 'PO 0274', None, None, 'International Environmental Policies', '01', 38734, 'Spring', 2019, 13, 25, 12, "['TF 0330pm-0445pm 01/22-04/30 DMH 350']"),
 ('Alphonso', 'Gwendoline M.', None, 'PO 0101', None, None, 'Introduction to American Politics', '01', 38717, 'Spring', 2019, 25, 25, 0, "['MR 1100am-1215pm 01/22-04/30 CNS 106']"),
 (' Patton', 'Martha Jane', None, 'PO 0102', None, None, 'Introduction to Comparative Politics', '01', 38719, 'Spring', 2019, 9, 25, 16, "['TF 0200pm-0315pm 01/22-04/30 DMH 231']"),
 ('Ramsey', 'Mark D.', None, 'CS 0333', None, None, 'Introduction to Cybersecurity', '01', 38885, 'Spring', 2019, 14, 20, 6, "['MW 0500pm-0615pm 01/22-04/30 BNW 131']"),
 (' Garcia Iommi', 'Lucrecia', None, 'PO 0104', None, None, 'Introduction to International Relations', '01', 38721, 'Spring', 2019, 10, 10, 0, "['TF 0930am-1045am 01/22-04/30 CNS 2']"),
 ('Cassidy', 'Kevin J.', None, 'PO 0103', None, None, 'Introduction to Political Ideas That Shape the World', '01', 38720, 'Spring', 2019, 23, 25, 2, "['MR 0930am-1045am 01/22-04/30 CNS 103']"),
 (' Patton', 'Martha Jane', None, 'PO 0255', None, None, 'Middle Eastern Politics', '01',

In [ ]:
('Fall2014','2014_2015'),
('Winter2015','2014_2015'),
('Spring2015','2014_2015'),
('Summer2015','2014_2015'),

('Fall2015','2015_2016'),
('Winter2016','2015_2016'),
('Spring2016','2015_2016'),
('Summer2016','2015_2016'),

('Fall2016','2016_2017'),
('Winter2017','2016_2017'),
('Spring2017','2016_2017'),
('SpringBreak2017','2016_2017'),
('Summer2017','2016_2017'),

('Fall2017','2017_2018'),
('Winter2018','2017_2018'),
('Spring2018','2017_2018'),
('Summer2018','2017_2018'),

('Fall2018','2018_2019'),
('Winter2019','2018_2019'),
('Spring2019','2018_2019')

In [8]:
%%sql
SELECT YEAR,SEMESTER ,SEMESTER|| '' ||YEAR as term,CatalogYear, COURSES_FACT.Catalog_ID,PROGRAMS_DIM.program_name,PROGRAMS_DIM.program_code,Title, CDDB.COURSE.credits, COURSE_CATALOGS_DIM.Prereqs, COURSE_CATALOGS_DIM.Coreqs, COURSE_CATALOGS_DIM.Fees,  COURSE_CATALOGS_DIM.Attributes, COURSE_CATALOGS_DIM.Description
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is NULL 




 * sqlite:///CourseDataWarehouse.db
Done.


[(2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0520', None, None, 'International Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0330', None, None, 'Auditing', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0330', None, None, 'Auditing', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0330', None, None, 'Auditing', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC0

In [9]:

missing_df = _.DataFrame()

missing_df.head()




YEAR SEMESTER        term CatalogYear Catalog_ID program_name  \
0  2014.0     Fall    Fall2014        None     AC0011         None   
1  2014.0     Fall    Fall2014        None     AC0011         None   
2  2014.0     Fall    Fall2014        None     AC0011         None   
3  2015.0   Spring  Spring2015        None     AC0520         None   
4  2015.0   Spring  Spring2015        None     AC0012         None   

  program_code                                  Title credits Prereqs Coreqs  \
0         None   Introduction to Financial Accounting    None    None   None   
1         None   Introduction to Financial Accounting    None    None   None   
2         None   Introduction to Financial Accounting    None    None   None   
3         None               International Accounting    None    None   None   
4         None  Introduction to Management Accounting    None    None   None   

   Fees Attributes Description  
0  None       None        None  
1  None       None        None  
2  None       None        None  
3  None       None        None  
4  None       None        None

In [10]:
missing_df.shape

(3208, 14)

In [11]:
missing_df = _.DataFrame()

missing_df.head()

term_lst= ['Fall2016','Winter2017' , 'Spring2017' ,'Summer2017'  ,'SpringBreak2017']



df = missing_df[missing_df.term.isin(term_lst)]

df = df[df.duplicated(['Catalog_ID'])==False].sort_values('Catalog_ID')

df['CatalogYear'] = '2016_2017'
df.to_csv('CourseCatalog2016_2017.csv')




In [12]:
df[df.duplicated(['Catalog_ID'])==False].sort_values('Catalog_ID')

YEAR SEMESTER        term CatalogYear Catalog_ID program_name  \
3166  2017.0   Spring  Spring2017        None    AC0585B         None   
139   2017.0   Spring  Spring2017        None    AY0390A         None   
591   2017.0   Spring  Spring2017        None    CO0248H         None   
1100  2016.0     Fall    Fall2016        None   ENW0207C         None   
2893  2016.0     Fall    Fall2016        None     FE0001         None   
3053  2016.0     Fall    Fall2016        None    FT0568E         None   
1459  2016.0     Fall    Fall2016        None    IS0585C         None   
1821  2017.0   Summer  Summer2017        None    MA0495B         None   
2890  2017.0   Summer  Summer2017        None     MD0099         None   
3084  2017.0   Summer  Summer2017        None    MD0401A         None   
2803  2016.0     Fall    Fall2016        None    MD0403A         None   
2892  2016.0     Fall    Fall2016        None     MD0433         None   
2222  2017.0   Spring  Spring2017        None    PH0299C         None   
2338  2017.0   Spring  Spring2017        None    PO0190E         None   
3054  2017.0   Spring  Spring2017        None    PO0190F         None   
1117  2017.0   Spring  Spring2017        None    PO0190G         None   
2863  2016.0     Fall    Fall2016        None    PY0281B         None   
2865  2017.0   Spring  Spring2017        None    PY0281C         None   
2517  2017.0   Spring  Spring2017        None    RS0299C         None   
2693  2016.0     Fall    Fall2016        None     SE0500         None   
815   2017.0   Winter  Winter2017        None    SE0568A         None   
3077  2017.0   Spring  Spring2017        None     SW0201         None   
2551  2016.0     Fall    Fall2016        None     SW0202         None   
2596  2017.0   Spring  Spring2017        None     SW0205         None   
2761  2016.0     Fall    Fall2016        None    TA0300B         None   

     program_code                                              Title credits  \
3166         None        Special Topics Seminar: Forensic Accounting    None   
139          None        Special Topics: Introduction to Archaeology    None   
591          None  Health Communication for Healthcare Professionals    None   
1100         None  Themes in Creative Writing: Reading and Writin...    None   
2893         None                              First Year Experience    None   
3053         None          Special Topics: Small Business Management    None   
1459         None  Contemporary Topics: Database Systems for Busi...    None   
1821         None                       Special Topics: Graph Theory    None   
2890         None                                 Comprehensive Exam    None   
3084         None  Special Topics: Survey of Educational Technolo...    None   
2803         None                               The School Library I    None   
2892         None                     Critical Viewing of Television    None   
2222         None              Special Topics: Thomistic Metaphysics    None   
2338         None  Special Topics: Turkey: A Nation of Contradict...    None   
3054         None           Special Topics: State and Local Politics    None   
1117         None  Special Topics: Seminar on Global Environmenta...    None   
2863         None  Special Topics: Cross-Cultural Perspectives on...    None   
2865         None        Special Topics: Adult Development and Aging    None   
2517         None  Special Topics: Tradition and the Spirit of Pl...    None   
2693         None  Autism Spectrum Disorders: Theories and Interv...    None   
815          None  Special Topics: Instructional Strategies in th...    None   
3077         None                       Software Engineering Methods    None   
2551         None                            Software Design Methods    None   
2596         None                   Software Testing and Maintenance    None   
2761         None         Special Topics: Acting the Medical Patient    None   

     Prereqs Coreqs  Fees At

In [13]:
%%sql
SELECT DISTINCT COUNT(CRN), COUNT(CID), COUNT(CRN)
FROM COURSES_FACT;

 * sqlite:///CourseDataWarehouse.db
Done.


[(25525, 25525, 25525)]

In [14]:
# do we have enghe sections for students

In [15]:
%%sql

SELECT  Title , count(*) , count(FID) , sum(Act) ,sum(Cap), sum(Rem)  , YEAR 
FROM COURSES_FACT
left JOIN PROGRAMS_DIM USING (PID)
WHERE  Catalog_ID like "%IS%"
group by Title , YEAR 
having sum(Rem) <0
order by year desc
    

 * sqlite:///CourseDataWarehouse.db
Done.


[('Introduction to Information Systems', 7, 7, 181, 175, -6, 2019),
 ('Data Mining and Applications', 2, 2, 47, 45, -2, 2018),
 ('Fundamentals of Business Analytics', 2, 2, 55, 50, -5, 2017),
 ('Python for Business Analytics', 1, 1, 28, 20, -8, 2017),
 ('Contemporary Topics: Business Analytics with Spreadsheets', 1, 1, 1, 0, -1, 2016),
 ('Fundamentals of Web Design', 1, 1, 26, 25, -1, 2014),
 ('Intro to Information Systems', 10, 10, 237, 227, -10, 2014)]

In [24]:
%%sql

SELECT *
FROM COURSES_FACT
JOIN PROGRAMS_DIM USING (PID)
WHERE YEAR = 2017 and program_name like "%information%"
group by Title 


 * sqlite:///CourseDataWarehouse.db
Done.


[(8010, 32108, 'Spring', 2017, 'Business Analytics and Big Data Mgmt', '01', 17, 25, 8, "['R 0630pm-0930pm 03/08-04/26 DSB 114', 'S 0830am-0430pm 03/25-03/25 DSB 107', 'S 0830am-0430pm 04/08-04/08 DSB 107', 'S 0830am-0430pm 04/29-04/29 DSB 107']", 52, 92, 619, 'IS 0550', 'IS', 'Information Systems'),
 (13456, 32107, 'Spring', 2017, 'Data Mining and Business Intelligence', '01', 19, 25, 6, "['W 0630pm-0930pm 01/17-05/12 DSB 114']", 52, 92, 619, 'IS 0540', 'IS', 'Information Systems'),
 (923, 71341, 'Fall', 2017, 'Database Systems', '01', 23, 25, 2, "['TF 0330pm-0445pm 09/05-12/11 DSB 112']", 52, 7, 273, 'IS 0260', 'IS', 'Information Systems'),
 (1152, 72914, 'Fall', 2017, 'Databases for Business Analytics', '01', 18, 20, 2, "['T 0630pm-0930pm 10/31-12/12 DSB 115', 'S 0830am-0430pm 11/04-11/04 DSB 115', 'S 0830am-0430pm 11/18-11/18 DSB 115', 'S 0830am-0430pm 12/09-12/09 DSB 115']", 52, 9, 275, 'IS 0510', 'IS', 'Information Systems'),
 (924, 71287, 'Fall', 2017, 'E-Business Applications', '01', 19, 20, 1, "['W 1100am-0130pm 09/05-12/11 DSB 2109A']", 52, 10, 274, 'IS 0310', 'IS', 'Information Systems'),
 (7909, 31734, 'Spring', 2017, 'Fundamentals of Business Analytics', '01', 23, 25, 2, "['MR 0930am-1045am 01/17-05/02 CNS 301']", 52, 68, 431, 'IS 0210', 'IS', 'Information Systems'),
 (920, 71929, 'Fall', 2017, 'Fundamentals of Web Design', '01', 17, 20, 3, "['MR 0330pm-0445pm 09/05-12/11 DSB 109']", 52, 8, 274, 'IS 0135', 'IS', 'Information Systems'),
 (8008, 32651, 'Spring', 2017, 'Information Systems and Database Management', '01', 15, 25, 10, "['R 0630pm-0930pm 01/17-03/02 DSB 115', 'S 0830am-0430pm 01/28-01/28 DSB 115', 'S 0830am-0430pm 02/11-02/11 DSB 115', 'S 0830am-0430pm 02/25-02/25 DSB 115']", 52, 9, 619, 'IS 0500', 'IS', 'Information Systems'),
 (857, 71166, 'Fall', 2017, 'Introduction to Information Systems', '01', 30, 28, -2, "['TF 0930am-1045am 09/05-12/11 DSB 105']", 52, 1, 273, 'IS 0100', 'IS', 'Information Systems'),
 (8009, 32647, 'Spring', 2017, 'Project Management', '01', 14, 25, 11, "['T 0630pm-0930pm 03/07-04/25 DSB 105', 'S 0830am-0430pm 03/25-03/25 DSB 105', 'S 0830am-0430pm 04/08-04/08 DSB 105', 'S 0830am-0430pm 04/22-04/22 DSB 105']", 52, 1, 278, 'IS 0520', 'IS', 'Information Systems'),
 (1151, 72913, 'Fall', 2017, 'Python for Business Analytics', '01', 28, 20, -8, "['T 0630pm-0930pm 09/05-10/17 DSB 115', 'S 0830am-0430pm 09/09-09/09 DSB 115', 'S 0830am-0430pm 09/23-09/23 DSB 115', 'S 0830am-0430pm 10/07-10/07 DSB 115']", 52, 9, 275, 'IS 0505', 'IS', 'Information Systems'),
 (922, 71153, 'Fall', 2017, 'Systems Analysis and Logical Design', '01', 23, 25, 2, "['TF 1230pm-0145pm 09/05-12/11 DSB 110A']", 52, 3, 275, 'IS 0240', 'IS', 'Information Systems'),
 (7914, 32646, 'Spring', 2017, 'Systems Design and Implementation', '01', 7, 25, 18, "['W 0200pm-0430pm 01/17-05/02 DSB 2109A']", 52, 10, 275, 'IS 0320', 'IS', 'Information Systems')]

In [29]:
%%sql
vacuum; 

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [17]:
import pandas as pd
#https://datatofish.com/create-database-python-using-sqlite3/
from sqlalchemy import create_engine

engine = create_engine("sqlite:///CourseDataWarehouse.db")
#pick a table to load into a df

#load the table into a df  and give a condition( where, join)
query = ''' SELECT instructor_lname,instructor_fname,CatalogYear,  COURSES_FACT.Catalog_ID,program_name,program_code, Title ,SECTION  ,CRN, SEMESTER , YEAR , ACT, CAP,REM, TIMECODES
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC'''
tables = pd.read_sql_query(query,engine)
tables.shape

OperationalError: (sqlite3.OperationalError) no such column: CourseData.db
[SQL: ATTACH CourseData.db AS CDDB ; SELECT instructor_lname,instructor_fname,CatalogYear,  COURSES_FACT.Catalog_ID,program_name,program_code, Title ,SECTION  ,CRN, SEMESTER , YEAR , ACT, CAP,REM, TIMECODES
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC]
(Background on this error at: http://sqlalche.me/e/e3q8)

In [15]:
tables

instructor_lname instructor_fname Catalog_ID program_name program_code  \
0            Lakeland          Paul F.    RS 0268         None         None   
1             Cassidy         Kevin J.    PO 0233         None         None   
2             Bagirov            Feyzi    BA 0540         None         None   
3                  Li            Danke    HI 0102         None         None   
4                Rusu        Amalia I.   CS 0351L         None         None   
...               ...              ...        ...          ...          ...   
4365         LoMonaco        Martha S.    TA 0111         None         None   
4366            Huber         Sonya R.   ENW 0340         None         None   
4367        Silverman         Francine   ENW 0320         None         None   
4368         Humphrey          Hugh M.    RS 0220         None         None   
4369          Berwick          Tara M.       None         None         None   

                                  Title SECTION      CRN SEMESTER    YEAR  \
0             American Catholic History      01  38873.0   Spring  2019.0   
1            American Political Thought      01  38728.0   Spring  2019.0   
2                 Business Intelligence      01  39007.0   Spring  2019.0   
3              China, Japan, and Europe      01  38788.0   Spring  2019.0   
4     Computer Science Junior Clinic II      01  38886.0   Spring  2019.0   
...                                 ...     ...      ...      ...     ...   
4365    World Theatre: 1800 to Tomorrow       A  73009.0     Fall  2014.0   
4366              World of Publishing I       A  71658.0     Fall  2014.0   
4367          Writing the Feature Story       A  71099.0     Fall  2014.0   
4368                   Writings of Paul       A  72975.0     Fall  2014.0   
4369                               None    None      NaN     None     NaN   

       Act   Cap   Rem                                          timecodes  
0     25.0  25.0   0.0           ['TF 1100am-1215pm 01/22-04/30 CNS 304']  
1     22.0  25.0   3.0           ['MR 1100am-1215pm 01/22-04/30 CNS 103']  
2     30.0  30.0   0.0            ['R 0630pm-0930pm 03/25-05/10 DSB 115']  
3     25.0  25.0   0.0           ['TF 0200pm-0315pm 01/22-04/30 DMH 347']  
4      7.0  20.0  13.0            ['R 0930am-1020am 01/22-04/30 BNW 131']  
...    ...   ...   ...                                                ...  
4365  12.0  14.0   2.0  ['MR 1230pm-0120pm 09/02-12/08 DMH 149', 'W 12...  
4366  12.0  15.0   3.0           ['TF 1230pm-0145pm 09/02-12/08 DMH 131']  
4367   7.0  15.0   8.0            ['T 0700pm-0930pm 09/02-12/08 CNS 304']  
4368  25.0  25.0   0.0           ['TF 1230pm-0145pm 09/02-12/08 DMH 349']  
4369   NaN   NaN   NaN                                               None  

[4370 rows x 14 columns]

In [11]:
tables.to_csv("missing_Catalog_ID_all_info.csv")

In [31]:




import pandas as pd
#https://datatofish.com/create-database-python-using-sqlite3/
from sqlalchemy import create_engine

engine = create_engine("sqlite:///CourseDataWarehouse.db")
#pick a table to load into a df

#load the table into a df  and give a condition( where, join)
query = '''SELECT COURSES_FACT.Catalog_ID,program_name,program_code,Title, credits, Prereqs, Coreqs, Fees,  Attributes Description
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC'''
tables = pd.read_sql_query(query,engine)
tables.shape

(1, 8)

In [10]:
#tables.to_csv("missing_Catalog_ID_all_info4.csv")